阅读资料

- [Gaussic讲述卷积神经网络mnist](https://gaussic.github.io/2017/08/14/tensorflow-cnn/)
- [tensorflow中文社区](http://www.tensorfly.cn/tfdoc/tutorials/mnist_pros.html)

In [1]:
# 初始化工作
import tensorflow as tf

# 准备数据，mnist
old_v = tf.logging.get_verbosity()
tf.logging.set_verbosity(tf.logging.ERROR)

from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("../../data/mnist/", one_hot=True)

tf.logging.set_verbosity(old_v)

x = tf.placeholder("float", shape=[None, 784])
y_ = tf.placeholder("float", shape=[None, 10])

Extracting ../../data/mnist/train-images-idx3-ubyte.gz
Extracting ../../data/mnist/train-labels-idx1-ubyte.gz
Extracting ../../data/mnist/t10k-images-idx3-ubyte.gz
Extracting ../../data/mnist/t10k-labels-idx1-ubyte.gz


# 构建一个多层卷积网络

本小节在 mnist softmax 的基础上修改，构建一个多层卷积网络。最终大概达到 99.2% 的准确率。

## 权重初始化

多层卷积网络，需要创建大量的权重与偏置项。

- 权重需要在初始化时加入少量的噪声，以打破对称性以及避免0梯度。
- 本例使用 ReLu 神经元，即使用 线性整流函数（Rectified Linear Unit, ReLU）作为神经元的激活函数，所以建议使用一个较小的正数来初始化偏置项，避免神经元输出恒为0的问题(dead neurons)
- 预先定义两个函数用于初始化


In [2]:
# tf.truncated_normal(shape, mean, stddev)
# truncate 意译截断
# shape表示生成张量的维度，mean是均值，stddev是标准差。
# 这个函数产生正太分布，均值和标准差自己设定，并截断的产生正太分布。

def weight_variable(shape):
  initial = tf.truncated_normal(shape, stddev=0.1)
  return tf.Variable(initial)

def bias_variable(shape):
  initial = tf.constant(0.1, shape=shape) # 创建 shape 的 常量，并使用 value 填充
  return tf.Variable(initial)

## 第一层卷积

### 先认识 tf.nn.conv2d() 函数的使用

![](https://img-blog.csdn.net/20171229215216572?watermark/2/text/aHR0cDovL2Jsb2cuY3Nkbi5uZXQvTG9zZUluVmFpbg==/font/5a6L5L2T/fontsize/400/fill/I0JBQkFCMA==/dissolve/70/gravity/SouthEast)

```python
conv2d(
    input,
    filter,
    strides,
    padding,
    use_cudnn_on_gpu=None,
    data_format=None,
    name=None
)
```

- input 输入，4d参数 `[batch_size, in_height, in_width, n_channels]`，表示图片的批数，大小和通道。
- filter 过滤器，4d参数`[filter_height, filter_width, in_channels, out_channels]`，表示kernel的大小，输入通道数和输出通道数，其中输出通道数表示从上一层提取多少特征。
- strides 步长，1d参数，长度为4，其中`stride[0]`和`stride[3]`必须为1，一般格式为`[1, stride[1], stride[2], 1]`，在大部分情况下，因为在height和width上的步进设为一样，因此通常为`[1, stride, stride, 1]`。 
    + 计算公式为： 
    ```
    output[b,i,j,k]=∑di,dj,qinput[b,strides[1]∗i+di,strides[2]∗j+dj,q]∗filter[di,dj,q,k]
    ```
    
- padding 是一个字符串输入，分为 SAME 和 VALID 分别表示是否需要填充，因为卷积完之后因为周围的像素没有卷积到，因此一般是会出现卷积完的输出尺寸小于输入的现象的


### 第一层卷积的计算过程


第一层，由一个卷积接着一个 max pooling 完成，卷积在每个`5*5`的 patch 中算出32个特征。卷积的权重张量形状是`[5,5,1,32]`，前两个维度是 patch 的大小，接着是输入的通道数目，最后是输入的通道数目。而对于每一个输出通道都有一个对应的偏置量。

In [3]:
W_conv1 = weight_variable([5, 5, 1, 32]) # 权重即是卷积中的 filter
b_conv1 = bias_variable([32])

为了适应这一层卷积，输入 x 改为一个四维向量，第2,3维度对应图片的宽高，第4维度对应图片的颜色通道——灰度图为1 （如果是rgb彩色图，则为3）

In [4]:
x = tf.placeholder("float", [None, 784])
x_image = tf.reshape(x, [-1,28,28,1])

在这个实例里，我们会一直使用vanilla版本。我们的卷积使用1步长（stride size），0边距（padding size）的模板，保证输出和输入是同一个大小。我们的池化用简单传统的2x2大小的模板做max pooling。

In [5]:
def conv2d(x, W):
  return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
  return tf.nn.max_pool(x, ksize=[1, 2, 2, 1],
                        strides=[1, 2, 2, 1], padding='SAME')

我们把x_image和权值向量进行卷积，加上偏置项，然后应用ReLU激活函数，最后进行max pooling。

In [6]:
h_conv1 = tf.nn.relu(conv2d(x_image, W_conv1) + b_conv1) # 卷积的输出 + 偏移量 后，再经过 relu 置零张量中的负数
h_pool1 = max_pool_2x2(h_conv1) # 池化，提取特征

### 第二层卷积

为了构建一个更深的网络，我们会把几个类似的层堆叠起来。第二层中，每个5x5的patch会得到64个特征。

In [7]:
# 这里将第一层的 32 个特征，作为第二层的 32 个通道的输入，相应的，filter 的 depth = 32，有 64 个 filter，得出 64 个 depth 的输出
W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])

h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

### 密集连接层

现在，图片尺寸经过两层卷积中的池化后，从28x28减小到7x7，我们加入一个有1024个神经元的全连接层，用于处理整个图片。我们把池化层输出的张量reshape成一些向量，乘上权重矩阵，加上偏置，然后对其使用ReLU。

In [8]:
W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])

# 第二层卷积输出的 7*7*64 的张量，平铺成一维数组，分别与 1024 组 7*7*64 个数字相乘后相加，得出 1024 个输出，再加上偏移量、置零负数
h_pool2_flat = tf.reshape(h_pool2, [-1, 7*7*64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

### Dropout

为了减少过拟合，我们在输出层之前加入dropout。我们用一个placeholder来代表一个神经元的输出在dropout中保持不变的概率。这样我们可以在训练过程中启用dropout，在测试过程中关闭dropout。 TensorFlow的tf.nn.dropout操作除了可以屏蔽神经元的输出外，还会自动处理神经元输出值的scale。所以用dropout的时候可以不用考虑scale。

In [9]:
keep_prob = tf.placeholder("float") # 保留神经元的概率
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob) # 不同的训练过程中随机扔掉一部分神经元

### 输出层

最后，我们添加一个softmax层，就像前面的单层softmax regression一样。

In [10]:
W_fc2 = weight_variable([1024, 10])
b_fc2 = bias_variable([10])

y_conv=tf.nn.softmax(tf.matmul(h_fc1_drop, W_fc2) + b_fc2)

## 执行与评估

In [12]:
sess = tf.InteractiveSession()
cross_entropy = -tf.reduce_sum(y_*tf.log(y_conv))
train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
correct_prediction = tf.equal(tf.argmax(y_conv,1), tf.argmax(y_,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))
sess.run(tf.global_variables_initializer())
for i in range(20000):
  batch_xs, batch_ys = mnist.train.next_batch(50)
  if i%100 == 0:
    train_accuracy = accuracy.eval(feed_dict={
        x:batch_xs, y_: batch_ys, keep_prob: 1.0})
    print("step %d, training accuracy %g"%(i, train_accuracy))
  train_step.run(feed_dict={x: batch_xs, y_: batch_ys, keep_prob: 0.5})

print("test accuracy %g"%accuracy.eval(feed_dict={
    x: mnist.test.images, y_: mnist.test.labels, keep_prob: 1.0}))

Instructions for updating:
Use `tf.global_variables_initializer` instead.
step 0, training accuracy 0.06
step 100, training accuracy 0.76
step 200, training accuracy 0.9
step 300, training accuracy 0.94
step 400, training accuracy 0.96
step 500, training accuracy 0.98
step 600, training accuracy 0.92
step 700, training accuracy 0.96
step 800, training accuracy 0.94
step 900, training accuracy 0.96
step 1000, training accuracy 1
step 1100, training accuracy 1
step 1200, training accuracy 0.98
step 1300, training accuracy 0.94
step 1400, training accuracy 0.98
step 1500, training accuracy 0.98
step 1600, training accuracy 1
step 1700, training accuracy 0.98
step 1800, training accuracy 1
step 1900, training accuracy 0.98
step 2000, training accuracy 0.98
step 2100, training accuracy 0.88
step 2200, training accuracy 0.98
step 2300, training accuracy 0.98
step 2400, training accuracy 1
step 2500, training accuracy 0.98
step 2600, training accuracy 0.96
step 2700, training accuracy 1
step 

In [19]:
### 保存模型
saver = tf.train.Saver()
saver.save(sess, "../../MyModel/mnist_conv/", global_step=20000)

'../../MyModel/mnist_conv/-20000'